In [1]:
#Librerias necesarias para implementacion de algoritmo genetico
from __future__ import print_function

from evolver import Evolver

from tqdm import tqdm

import logging

import sys


# Aplicacion del Modelo
Aqui se aplica directamente el modelo descrito implementando el algoritmo genetico

In [2]:
#Librerias necesarias para trabajar con datasets
import pandas as pd
import numpy as np
from sklearn import linear_model, model_selection

#Librerias necesarias para aplicar redes neuronales
import tensorflow as tf
pd.set_option('display.max_columns', None)
df= pd.read_csv("Historial_Alumnos.csv", sep=",",index_col=False)
df.head()

id_anony Cod.Car.Sec  Cod.Car.Sec Codificado  Materia_1  \
0      2838  MCT-PLS13                     28.0  CALCULO 1   
1      4037  MCT-PLS13                     28.0  CALCULO 1   
2      4061  MCT-PLS13                     28.0  CALCULO 1   
3      4062  MCT-PLS13                     28.0  CALCULO 1   
4      4065  MCT-PLS13                     28.0  CALCULO 1   

   Materia_1 codificada  Anho_F_1  ciclo_F_1  Recursante_1  P1_F_1  P2_F_1  \
0                  33.0    2013.0        2.0           1.0     0.0    17.0   
1                  33.0    2015.0        2.0           1.0    16.0    19.0   
2                  33.0    2015.0        2.0           1.0    14.0    27.0   
3                  33.0    2015.0        2.0           1.0     5.0    24.0   
4                  33.0    2015.0        2.0           1.0    19.0    30.0   

   T_F_1  NotaFinal_1  Materia_1 Nota=1  Materia_1 Nota=2  Materia_1 Nota=3  \
0    8.0          2.0               0.0               1.0               0.0   
1    8.0          5.0               0.0               0.0               0.0   
2    8.0          3.0               0.0               0.0               1.0   
3    6.0          2.0               0.0               1.0               0.0   
4    9.0          5.0               0.0               0.0               0.0   

   Materia_1 Nota=4  Materia_1 Nota=5  Abandono la Materia 1  Materia_2  \
0               0.0               0.0                    1.0  CALCULO 2   
1               0.0               1.0                    0.0  CALCULO 2   
2               0.0               0.0                    0.0  CALCULO 2   
3               0.0               0.0                    0.0  CALCULO 2   
4               0.0               1.0                    0.0  CALCULO 2   

   Materia_2 codificada  Anho_F_2  ciclo_F_2  Recursante_2  P1_F_2  P2_F_2  \
0                  34.0    2014.0        1.0           1.0    11.0    16.0   
1                  34.0    2016.0        1.0           1.0    22.0    31.0   
2                  34.0    2016.0        1.0           1.0    13.0    23.0   
3                  34.0    2016.0        1.0           1.0    21.0    19.0   
4                  34.0    2016.0        1.0           1.0    24.0    29.0   

   T_F_2  NotaFinal_2  Materia_2 Nota=1  Materia_2 Nota=2  Materia_2 Nota=3  \
0    8.0          2.0               0.0               1.0               0.0   
1    7.0          5.0               0.0               0.0               0.0   
2    5.0          2.0               0.0               1.0               0.0   
3    5.0          2.0               0.0               1.0               0.0   
4    9.0          5.0               0.0               0.0               0.0   

   Materia_2 Nota=4  Materia_2 Nota=5  Abandono la Materia 2  Materia_3  \
0               0.0               0.0                    0.0  CALCULO 3   
1               0.0               1.0                    0.0  CALCULO 3   
2               0.0               0.0                    0.0  CALCULO 3   
3               0.0               0.0                    0.0  CALCULO 3   
4               0.0               1.0                    0.0  CALCULO 3   

   Materia_3 codificada  Anho_F_3  ciclo_F_3  Recursante_3  P1_F_3  P2_F_3  \
0                  35.0    2016.0        2.0           1.0    10.0     7.0   
1                  35.0    2016.0        2.0           1.0     6.0     9.0   
2                  35.0    2016.0        2.0           1.0    17.0    10.0   
3                  35.0    2016.0        2.0           1.0     5.0    18.0   
4                  35.0    2016.0        2.0           1.0    22.0    20.0   

   T_F_3  NotaFinal_3  Materia_3 Nota=1  Materia_3 Nota=2  Materia_3 Nota=3  \
0    2.0          2.0               0.0               1.0               0.0   
1    8.0          4.0               0.0               0.0               0.0   
2    8.0          2.0               0.0               1.0               0.0   
3    6.0          2.0               0.0               1

Antes que nada, es necesario preparar los datos que la red neuronal solicita para poder procesar la opcion mas viable para nuestro analisis

In [3]:
data=df[['Materia_1 codificada','Anho_F_1','ciclo_F_1','Recursante_1','P1_F_1','P2_F_1','T_F_1','NotaFinal_1','Abandono la Materia 1','Materia_2 codificada','Anho_F_2','ciclo_F_2','Recursante_2','P1_F_2','P2_F_2','T_F_2','NotaFinal_2','Abandono la Materia 2']]

[filas,columnas]=data.shape
labels=df[['Materia_3 Nota=5']]

#Como labels figura como string, es necesario cambiarlos a valores enteros
data = np.array(data)
labels = np.array(labels)
labels=np.ravel(labels)

#Verificamos las dimensiones de data y labels
display(np.shape(labels))
display(np.shape(data))

(56,)

(56, 18)

Los datos que el algoritmo genetico solicita a lo largo de su procesamiento son data, labels y columnas. Para facilitar dichos datos del notebook al algoritmo genetico, se emplea la libreria pickle

In [4]:
from pickle import dump,load
dump(data, open('data.pkl', 'wb'))
dump(labels, open('labels.pkl', 'wb'))
dump(columnas, open('columnas.pkl', 'wb'))

Una vez definidos apropiadamente estos parametros, se procede a realizar el procesamiento con el algoritmo genetico

In [5]:
import main as ge
lista=ge.main()

07/07/2021 10:25:28 AM - INFO - ***generate(generations, population, all_possible_genes, dataset)***
07/07/2021 10:25:28 AM - INFO - ***Now in generation 1 of 50***
07/07/2021 10:25:28 AM - INFO - --------------------------------------------------------------------------------
07/07/2021 10:25:28 AM - INFO - {'nb_layers': 4, 'activation': 'softmax', 'optimizer': 'adamax', 'nb_neurons': [16, 16, 64, 128, 128, 32]}
07/07/2021 10:25:28 AM - INFO - Acc: 0.00%
07/07/2021 10:25:28 AM - INFO - UniID: 1
07/07/2021 10:25:28 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:25:28 AM - INFO - Gen: 1
07/07/2021 10:25:28 AM - INFO - Hash: d7128504af1c696f8cbadf119d6e38a7
07/07/2021 10:25:28 AM - INFO - {'nb_layers': 2, 'activation': 'relu', 'optimizer': 'adamax', 'nb_neurons': [64, 32, 64, 128, 16, 64]}
07/07/2021 10:25:28 AM - INFO - Acc: 0.00%
07/07/2021 10:25:28 AM - INFO - UniID: 2
07/07/2021 10:25:28 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:25:28 AM - INFO - Gen: 1
07/07/2021 10:25:28 AM - INFO - H

07/07/2021 10:25:28 AM - INFO - {'nb_layers': 5, 'activation': 'softmax', 'optimizer': 'adamax', 'nb_neurons': [128, 32, 16, 64, 16, 128]}
07/07/2021 10:25:28 AM - INFO - Acc: 0.00%
07/07/2021 10:25:28 AM - INFO - UniID: 22
07/07/2021 10:25:28 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:25:28 AM - INFO - Gen: 1
07/07/2021 10:25:28 AM - INFO - Hash: 6b5e17e451cc2c96712d351427d27e4a
07/07/2021 10:25:28 AM - INFO - {'nb_layers': 5, 'activation': 'relu', 'optimizer': 'adam', 'nb_neurons': [16, 64, 16, 64, 32, 16]}
07/07/2021 10:25:28 AM - INFO - Acc: 0.00%
07/07/2021 10:25:28 AM - INFO - UniID: 23
07/07/2021 10:25:28 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:25:28 AM - INFO - Gen: 1
07/07/2021 10:25:28 AM - INFO - Hash: 0447d31cb4c16b24b3d763ab782b0e44
07/07/2021 10:25:28 AM - INFO - {'nb_layers': 1, 'activation': 'relu', 'optimizer': 'adam', 'nb_neurons': [64, 16, 16, 16, 16, 32]}
07/07/2021 10:25:28 AM - INFO - Acc: 0.00%
07/07/2021 10:25:28 AM - INFO - UniID: 24
07/07/2021 10:25:28 AM -

***Dataset: dataset
***Evolving for 50 generations with population size = 30***
(44,)
(44, 18)
(44, 2)
(44, 18)
(44, 18)
(44, 2)
Epoch 1/50
1/1 [==============================] - 0s 159ms/step - loss: 0.6940 - accuracy: 0.4545 - val_loss: 0.6930 - val_accuracy: 0.5833
Epoch 2/50
1/1 [==============================] - 0s 12ms/step - loss: 0.6939 - accuracy: 0.4773 - val_loss: 0.6931 - val_accuracy: 0.5833
Epoch 3/50
1/1 [==============================] - 0s 12ms/step - loss: 0.6938 - accuracy: 0.4091 - val_loss: 0.6933 - val_accuracy: 0.4167


  3%|▎         | 1/30 [00:01<00:34,  1.19s/it]07/07/2021 10:25:29 AM - INFO - Getting Keras datasets
07/07/2021 10:25:29 AM - INFO - Compling Keras model
07/07/2021 10:25:29 AM - INFO - Architecture:[64, 32, 64, 128, 16, 64],relu,adamax,2


Test loss: 0.6932675242424011
Test accuracy: 0.4166666567325592

 Modelo mas eficiente creado 

(44,)
(44, 18)
(44, 2)
(44, 18)
(44, 18)
(44, 2)
Epoch 1/50
1/1 [==============================] - 0s 107ms/step - loss: 0.6962 - accuracy: 0.4773 - val_loss: 0.6776 - val_accuracy: 0.5833
Epoch 2/50
1/1 [==============================] - 0s 11ms/step - loss: 0.7200 - accuracy: 0.4545 - val_loss: 0.6760 - val_accuracy: 0.5833
Epoch 3/50
1/1 [==============================] - 0s 11ms/step - loss: 0.7070 - accuracy: 0.4318 - val_loss: 0.6745 - val_accuracy: 0.5833
Test loss: 0.6745009422302246
Test accuracy: 0.5833333134651184

 Modelo mas eficiente creado 



...

07/07/2021 10:51:17 AM - WARNING - 5 out of the last 13 calls to <function Model.make_train_function.<locals>.train_function at 0x000001E799D4F5E0> triggered tf.function retracing. Tracing is expensive and the excessive number of tracings could be due to (1) creating @tf.function repeatedly in a loop, (2) passing tensors with different shapes, (3) passing Python objects instead of tensors. For (1), please define your @tf.function outside of the loop. For (2), @tf.function has experimental_relax_shapes=True option that relaxes argument shapes that can avoid unnecessary retracing. For (3), please refer to https://www.tensorflow.org/tutorials/customization/performance#python_or_tensor_args and https://www.tensorflow.org/api_docs/python/tf/function for  more details.


1/1 [==============================] - 0s 112ms/step - loss: 0.6932 - accuracy: 0.5909 - val_loss: 0.7285 - val_accuracy: 0.4167
Epoch 2/50
1/1 [==============================] - 0s 10ms/step - loss: 0.7049 - accuracy: 0.5000 - val_loss: 0.7220 - val_accuracy: 0.4167
Epoch 3/50
1/1 [==============================] - 0s 10ms/step - loss: 0.7179 - accuracy: 0.5000 - val_loss: 0.7164 - val_accuracy: 0.4167


100%|██████████| 55/55 [00:33<00:00,  1.64it/s]
07/07/2021 10:51:17 AM - INFO - Generation average: 52.73%
07/07/2021 10:51:17 AM - INFO - --------------------------------------------------------------------------------
07/07/2021 10:51:17 AM - INFO - --------------------------------------------------------------------------------
07/07/2021 10:51:17 AM - INFO - {'activation': 'relu', 'nb_layers': 4, 'optimizer': 'adamax', 'nb_neurons': [16, 16, 128, 32, 32, 128]}
07/07/2021 10:51:17 AM - INFO - Acc: 83.33%
07/07/2021 10:51:17 AM - INFO - UniID: 55
07/07/2021 10:51:17 AM - INFO - Mom and Dad: 8 2
07/07/2021 10:51:17 AM - INFO - Gen: 2
07/07/2021 10:51:17 AM - INFO - Hash: e57864a3ced9551f13a7a5a071b2c22f
07/07/2021 10:51:17 AM - INFO - {'activation': 'softmax', 'nb_layers': 1, 'optimizer': 'adam', 'nb_neurons': [128, 32, 16, 16, 32, 32]}
07/07/2021 10:51:17 AM - INFO - Acc: 83.33%
07/07/2021 10:51:17 AM - INFO - UniID: 306
07/07/2021 10:51:17 AM - INFO - Mom and Dad: 262 171
07/07/2021

Test loss: 0.7164395451545715
Test accuracy: 0.4166666567325592


07/07/2021 10:51:17 AM - INFO - {'activation': 'relu', 'nb_layers': 1, 'optimizer': 'adam', 'nb_neurons': [128, 64, 16, 16, 64, 32]}
07/07/2021 10:51:17 AM - INFO - Acc: 83.33%
07/07/2021 10:51:17 AM - INFO - UniID: 1241
07/07/2021 10:51:17 AM - INFO - Mom and Dad: 1098 613
07/07/2021 10:51:17 AM - INFO - Gen: 39
07/07/2021 10:51:17 AM - INFO - Hash: 8d2ac0696e00bcebacec11ba5666941c
